In [1]:
# adding bytetree filters
def add_cme_expiry(temp):
  # cme expiry
  temp['datetime'] = pd.to_datetime(temp.index)
  # this might get some wrong?
  temp['cme_expiry'] = (temp.datetime.dt.day > temp.datetime.dt.days_in_month-7) & (temp.datetime.dt.weekday == 4)
  # temp['cme_expiry'] = temp.datetime.dt.day == 1
  return temp

def time_since_marker(df, column, cap=None):
    steps = 0
    step_list = []
    for isadj in df[column].tolist():
        steps += 1
        if isadj:
            steps = 0
        if cap and steps > cap:
            steps = 0
        step_list.append(steps)
    return pd.Series(step_list).values

DIF_ADJ_BLOCKS = 2016
def add_dif_adj_h(df):
    df['DiffChanged'] = abs(df['dif'] - df['dif'].shift(1)) > 0.0
    # 144 should be one days worth of blocks
    df['BlockAdjustment'] = df['hgt'] % DIF_ADJ_BLOCKS == 0
    print (df.loc[df.DiffChanged, ['DiffChanged', 'BlockAdjustment', 'time']].tail(500))
    return df

# prep daily byteree
def add_dif_adj(df):
    df['DiffChanged'] = abs(df['dif'] - df['dif'].shift(1)) > 0.0
    # 144 should be one days worth of blocks
    df['BlockAdjustment'] = df['hgt'] % DIF_ADJ_BLOCKS < 144
    return df

In [2]:
# trying to consolidate colab FFT_Norm notebook locally
# !pip install scaleogram
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import plotly.express as px
from preprocess import normalise_data, detrend, preprocess_frame
## from preprocess import add_cme_expiry

df = pd.read_csv("DATASET.CSV")
df = preprocess_frame(df)
print (df.tail())

fig = px.line(x=df.index, y=df.Close, log_y=True)
fig

                     Symbol     Open     High      Low    Close  Volume BTC  \
Date                                                                          
2019-11-04 06:00:00  BTCUSD  9146.71  9179.47  9136.19  9165.70       39.45   
2019-11-04 07:00:00  BTCUSD  9165.70  9206.95  9158.58  9190.00      110.28   
2019-11-04 08:00:00  BTCUSD  9190.00  9195.00  9151.23  9163.58       79.20   
2019-11-04 09:00:00  BTCUSD  9163.58  9187.45  9152.43  9175.00       88.15   
2019-11-04 10:00:00  BTCUSD  9175.00  9200.59  9175.00  9200.59        0.00   

                     Volume USD  Range    Value  Returns  PercentChange  \
Date                                                                      
2019-11-04 06:00:00   361470.51  43.28  9165.70    18.99       0.002076   
2019-11-04 07:00:00  1012811.02  48.37  9190.00    24.30       0.002651   
2019-11-04 08:00:00   727035.14  43.77  9163.58   -26.42      -0.002875   
2019-11-04 09:00:00   808431.33  35.02  9175.00    11.42       0.001246

In [5]:
import plotly.express as px
from plotly.subplots import make_subplots

def seasonal_violin(df, x_col, y_col):
    # fig = px.violin(df, y=y_col, x=x_col, box=True, points='all')
    fig = px.box(df, y=y_col, x=x_col) # , points='all'
    return fig

def seasonal_index_plot(df, x_col, y_col, use_violin=False):
    if use_violin:
        fig = make_subplots(rows=3, cols=1, shared_xaxes=True)
        fig1 = px.violin(df, y=y_col, x=x_col, box=True, points='all')
        fig.add_trace(fig1['data'][0], row=3, col=1)
    else:
        fig = make_subplots(rows=2, cols=1, shared_xaxes=True)

    df_pv = pd.pivot_table(df, index=[x_col], values=[y_col], aggfunc=['mean', 'median', 'std'])
    mean_line = df_pv[[('mean', y_col)]].values
    upper_band = mean_line + df_pv[[('std', y_col)]].values
    lower_band = mean_line - df_pv[[('std', y_col)]].values
    
    fig.add_scatter(x=df_pv.index, y=mean_line[:, 0], name="mean", row=2, col=1)
    fig.add_scatter(x=df_pv.index, y=upper_band[:, 0], name="upper", row=2, col=1)
    fig.add_scatter(x=df_pv.index, y=lower_band[:, 0], name="lower", row=2, col=1)
    
    # can hide legend in BB, but nice
    fig.add_scatter(x=df_pv.index, y=mean_line[:, 0], name="mean", row=1, col=1)
    
    # fig.show()
    return fig

# event based, TODO split into cells
if False:
    # daily block adjustment
    REC_EVENT_COL = "BlockAdjustment"
    VALUE_COL = "PercentChange"
    df = add_dif_adj(df)
    CAP = 14
elif False:
    # hourly block adjustment
    REC_EVENT_COL = "BlockAdjustment"
    VALUE_COL = "PercentChange"
    df = add_dif_adj_h(df)
    CAP = DIF_ADJ_BLOCKS
elif True:
    # daily cme expiry
    REC_EVENT_COL = "cme_expiry"
    # VALUE_COL = "Close"
    # VALUE_COL = "PercentChange"
    VALUE_COL = "Returns"
    df = add_cme_expiry(df)
    CAP = 31

if True:
    # show marker locations
    fig = px.line(x=df.index, y=df.Close, log_y=True)
    marks = df[df[REC_EVENT_COL]==True]
    fig.add_scatter(x=marks.index, y=marks.Close, mode="markers", marker=dict(size=10, symbol=5, color="green"), name="Marker")    
    fig.show()
    
    df["bars_elapsed"] = time_since_marker(df, REC_EVENT_COL, cap=CAP) # , cap=DIF_ADJ_BLOCKS, cap=15, cap=31
    # df = df[df['bars_elapsed'] < CAP]
    df = df[pd.notnull(df['bars_elapsed'])]

# seasonal_index_plot(df, x_col="bars_elapsed", y_col=VALUE_COL).show()
# seasonal_index_plot(df, x_col="Doy", y_col="PercentChange")
# seasonal_index_plot(df, x_col="Hour", y_col="PercentChange").show()


In [11]:
# hourly kill zones
VALUE_COL = "PercentChange"
seasonal_index_plot(df, x_col="Hour", y_col=VALUE_COL).show()
seasonal_violin(df, x_col="Hour", y_col=VALUE_COL).show()

In [ ]:
# Date Formatting or Changing Tick labels
# https://plotly.com/python/tick-formatting/
# tickmode = 'array', but still tricky for yearly
# plotting one sample year with date ticks and averages on shared xaxis?

fig.update_layout(
    xaxis = dict(
        tickmode = 'array',
        tickvals = [(x+1)*30 for x in range(12)],
        ticktext = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
    )
)
fig.show()
for x in zip([(x+1)*28 for x in range(12)], ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']):
    print (x)